In [24]:
# -*- coding: utf-8 -*-

from geopandas import GeoDataFrame
from shapely.geometry import MultiPoint, Point
from movingpandas.trajectory import Trajectory
from movingpandas.trajectory_collection import TrajectoryCollection
from movingpandas.geometry_utils import mrr_diagonal
from movingpandas.trajectory_utils import convert_time_ranges_to_segments
from movingpandas.time_range_utils import TemporalRangeWithTrajId


class TrajectoryStopDetector:
    """
    Detects stops in a trajectory.
    A stop is detected if the movement stays within an area of specified size for
    at least the specified duration.
    """

    def __init__(self, traj):
        """
        Create StopDetector

        Parameters
        ----------
        traj : Trajectory or TrajectoryCollection
        """
        self.traj = traj

    def get_stop_time_ranges(self, max_diameter, min_duration):
        """
        Returns detected stop start and end times

        Parameters
        ----------
        max_diameter : float
            Maximum diameter for stop detection
        min_duration : datetime.timedelta
            Minimum stop duration

        Returns
        -------
        list
            TemporalRanges of detected stops
        """
        if isinstance(self.traj, Trajectory):
            return self._process_traj(self.traj, max_diameter, min_duration)
        elif isinstance(self.traj, TrajectoryCollection):
            return self._process_traj_collection(max_diameter, min_duration)
        else:
            raise TypeError

    def _process_traj_collection(self, max_diameter, min_duration):
        result = []
        for traj in self.traj:
            for time_range in self._process_traj(traj, max_diameter, min_duration):
                result.append(time_range)
        return result

    def _process_traj(self, traj, max_diameter, min_duration):
        detected_stops = []
        segment_geoms = []
        segment_times = []
        geom = MultiPoint()
        is_stopped = False
        previously_stopped = False

        for index, data in traj.df[traj.get_geom_column_name()].items():
            segment_geoms.append(data)
            print("segment_geoms = " + str(segment_geoms))
            geom = geom.union(data)
            print("geom = " + str(geom))
            segment_times.append(index)

            if not is_stopped:  # remove points to the specified min_duration
                print("Not stopped")
                while (
                    len(segment_geoms) > 2
                    and segment_times[-1] - segment_times[0] >= min_duration
                ):
                    print("segment_geoms>2, segment_times diff > min duration, deleting values")
                    segment_geoms.pop(0)
                    segment_times.pop(0)
                # after removing extra points, re-generate geometry
                geom = MultiPoint(segment_geoms)
                print("segment_geoms = " + str(segment_geoms))

            if (
                len(segment_geoms) > 1
                and mrr_diagonal(geom, traj.is_latlon) < max_diameter
            ):
                is_stopped = True
                print("is_stopped set to True")
            else:
                is_stopped = False
                print("is_stopped set to False")

            if len(segment_geoms) > 1:
                print("len segment_geoms>1, setting segment begin and end")
                segment_end = segment_times[-2]
                segment_begin = segment_times[0]
                if not is_stopped and previously_stopped:
                    print("is_stopped = " + str(is_stopped) + ", previously stopped = " + str(previously_stopped))
                    if (
                        segment_end - segment_begin >= min_duration
                    ):  # detected end of a stop
                        print("segment end - segment_begin >= min_duration, appending")
                        detected_stops.append(
                            TemporalRangeWithTrajId(segment_begin, segment_end, traj.id)
                        )
                        segment_geoms = []
                        print("segment_geoms = " + str(segment_geoms))
                        segment_times = []
                        geom = MultiPoint()
                        print("geom = " + str(geom))

            previously_stopped = is_stopped
            print("setting previously_stopped = " + str(is_stopped))

        if is_stopped and segment_times[-1] - segment_times[0] >= min_duration:
            print("segment end - segment_begin >= min_duration, appending")
            detected_stops.append(
                TemporalRangeWithTrajId(segment_times[0], segment_times[-1], traj.id)
            )

        return detected_stops

    def get_stop_segments(self, max_diameter, min_duration):
        """
        Returns detected stop trajectory segments

        Parameters
        ----------
        max_diameter : float
            Maximum diameter for stop detection
        min_duration : datetime.timedelta
            Minimum stop duration

        Returns
        -------
        TrajectoryCollection
            Trajectory segments

        Examples
        --------

        >>> detector = mpd.TrajectoryStopDetector(traj)
        >>> stops = detector.get_stop_segments(min_duration=timedelta(seconds=60),
                                               max_diameter=100)
        """
        stop_time_ranges = self.get_stop_time_ranges(max_diameter, min_duration)
        return TrajectoryCollection(
            convert_time_ranges_to_segments(self.traj, stop_time_ranges)
        )

    def get_stop_points(self, max_diameter, min_duration):
        """
        Returns detected stop location points

        Parameters
        ----------
        max_diameter : float
            Maximum diameter for stop detection
        min_duration : datetime.timedelta
            Minimum stop duration

        Returns
        -------
        geopandas.GeoDataFrame
            Stop locations as points with start and end time and stop duration
            in seconds

        Examples
        --------

        >>> detector = mpd.TrajectoryStopDetector(traj)
        >>> stops = detector.get_stop_points(min_duration=timedelta(seconds=60),
                                             max_diameter=100)
        """
        stop_time_ranges = self.get_stop_time_ranges(max_diameter, min_duration)
        stops = TrajectoryCollection(
            convert_time_ranges_to_segments(self.traj, stop_time_ranges)
        )

        stop_pts = GeoDataFrame(columns=["geometry"]).set_geometry("geometry")
        stop_pts["stop_id"] = [track.id for track in stops.trajectories]
        stop_pts = stop_pts.set_index("stop_id")

        for stop in stops:
            stop_pts.at[stop.id, "start_time"] = stop.get_start_time()
            stop_pts.at[stop.id, "end_time"] = stop.get_end_time()
            pt = Point(stop.df.geometry.x.median(), stop.df.geometry.y.median())
            stop_pts.at[stop.id, "geometry"] = pt
            stop_pts.at[stop.id, "traj_id"] = stop.parent.id

        if len(stops) > 0:
            stop_pts["duration_s"] = (
                stop_pts["end_time"] - stop_pts["start_time"]
            ).dt.total_seconds()
            stop_pts["traj_id"] = stop_pts["traj_id"].astype(type(stop.parent.id))

        return stop_pts


In [20]:
import geopandas as gpd
import hvplot.pandas 
from datetime import datetime, timedelta

In [21]:
gpx = 'GPX/2023/301_to_Raheen.gpx'
bus_stops = gpd.read_file("GPKG/stops_304_to_UL.gpkg")
journey_plot_title = '304 to UL 2023-03-09 08:11'

In [22]:
gdf = gpd.read_file(gpx, layer='track_points').set_index('time')
gdf.drop(columns=['magvar', 'geoidheight', 'name', 'cmt', 'desc',
       'src', 'link1_href', 'link1_text', 'link1_type', 'link2_href', 
       'link2_text', 'link2_type', 'sym', 'type', 'fix', 'sat', 'hdop', 'vdop',
       'pdop', 'ageofdgpsdata', 'dgpsid'], inplace=True) 
track = Trajectory(gdf, 1)
track.add_speed(overwrite="True")
track.add_distance(overwrite="True")
track.df['speed_kph'] = track.df['speed'] * 3.6

In [25]:
detector = TrajectoryStopDetector(track)
stationary_points = detector.get_stop_points(min_duration=timedelta(seconds=15), max_diameter=30)

segment_geoms = [<POINT (-8.599 52.682)>]
geom = POINT (-8.599094 52.682488)
Not stopped
segment_geoms = [<POINT (-8.599 52.682)>]
is_stopped set to False
setting previously_stopped = False
segment_geoms = [<POINT (-8.599 52.682)>, <POINT (-8.599 52.683)>]
geom = MULTIPOINT (-8.599094 52.682488, -8.599154 52.682506)
Not stopped
segment_geoms = [<POINT (-8.599 52.682)>, <POINT (-8.599 52.683)>]
is_stopped set to True
len segment_geoms>1, setting segment begin and end
setting previously_stopped = True
segment_geoms = [<POINT (-8.599 52.682)>, <POINT (-8.599 52.683)>, <POINT (-8.599 52.683)>]
geom = MULTIPOINT (-8.599094 52.682488, -8.599154 52.682506, -8.599209 52.682516)
is_stopped set to True
len segment_geoms>1, setting segment begin and end
setting previously_stopped = True
segment_geoms = [<POINT (-8.599 52.682)>, <POINT (-8.599 52.683)>, <POINT (-8.599 52.683)>, <POINT (-8.599 52.683)>]
geom = MULTIPOINT (-8.599094 52.682488, -8.599154 52.682506, -8.599209 52.682516, -8.599261 52.6

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [26]:
stop_time_ranges = detector.get_stop_time_ranges(min_duration=timedelta(seconds=15), max_diameter=30)
for x in stop_time_ranges: 
    print(x)

segment_geoms = [<POINT (-8.599 52.682)>]
geom = POINT (-8.599094 52.682488)
Not stopped
segment_geoms = [<POINT (-8.599 52.682)>]
is_stopped set to False
setting previously_stopped = False
segment_geoms = [<POINT (-8.599 52.682)>, <POINT (-8.599 52.683)>]
geom = MULTIPOINT (-8.599094 52.682488, -8.599154 52.682506)
Not stopped
segment_geoms = [<POINT (-8.599 52.682)>, <POINT (-8.599 52.683)>]
is_stopped set to True
len segment_geoms>1, setting segment begin and end
setting previously_stopped = True
segment_geoms = [<POINT (-8.599 52.682)>, <POINT (-8.599 52.683)>, <POINT (-8.599 52.683)>]
geom = MULTIPOINT (-8.599094 52.682488, -8.599154 52.682506, -8.599209 52.682516)
is_stopped set to True
len segment_geoms>1, setting segment begin and end
setting previously_stopped = True
segment_geoms = [<POINT (-8.599 52.682)>, <POINT (-8.599 52.683)>, <POINT (-8.599 52.683)>, <POINT (-8.599 52.683)>]
geom = MULTIPOINT (-8.599094 52.682488, -8.599154 52.682506, -8.599209 52.682516, -8.599261 52.6

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)

